# Final project of Agents course: An Agent that response the GAIA benchmark

In this notebook, **we're going to read the GAIA questions from metadata and we'll store in a chroma database to use as retriever**.

This notebook is part of the <a href="https://www.hf.co/learn/agents-course">Hugging Face Agents Course</a>, a free course from beginner to expert, where you learn to build Agents.

## What we'll do

In this notebook, we'll do:

1. Reading json metadata with GAIA questions
2. Creating chroma vector store
3. Querying the database and converting to a retriever to search using


In [ ]:
import os
import json
from dotenv import load_dotenv
from langchain_huggingface import HuggingFaceEmbeddings
from langchain_chroma import Chroma
import random

# from langchain.schema import Document
from langchain_core.documents import Document
from uuid import uuid4

load_dotenv()


True

In [2]:
os.chdir(os.path.abspath(".."))

<div style="background-color:lightblue; color:black; font-weight:bold">

## 1. Reading json metadata

</div>


In [3]:
# Load the metadata.jsonl file
with open("data/metadata.jsonl", "r") as jsonl_file:
    json_list = list(jsonl_file)

json_QA = []
for json_str in json_list:
    json_data = json.loads(json_str)
    json_QA.append(json_data)


In [ ]:
# randomly select 3 samples
# {"task_id": "c61d22de-5f6c-4958-a7f6-5e9707bd3466", "Question": "A paper about AI regulation that was originally submitted to arXiv.org in June 2022 shows a figure with three axes, where each axis has a label word at both ends. Which of these words is used to describe a type of society in a Physics and Society article submitted to arXiv.org on August 11, 2016?", "Level": 2, "Final answer": "egalitarian", "file_name": "", "Annotator Metadata": {"Steps": "1. Go to arxiv.org and navigate to the Advanced Search page.\n2. Enter \"AI regulation\" in the search box and select \"All fields\" from the dropdown.\n3. Enter 2022-06-01 and 2022-07-01 into the date inputs, select \"Submission date (original)\", and submit the search.\n4. Go through the search results to find the article that has a figure with three axes and labels on each end of the axes, titled \"Fairness in Agreement With European Values: An Interdisciplinary Perspective on AI Regulation\".\n5. Note the six words used as labels: deontological, egalitarian, localized, standardized, utilitarian, and consequential.\n6. Go back to arxiv.org\n7. Find \"Physics and Society\" and go to the page for the \"Physics and Society\" category.\n8. Note that the tag for this category is \"physics.soc-ph\".\n9. Go to the Advanced Search page.\n10. Enter \"physics.soc-ph\" in the search box and select \"All fields\" from the dropdown.\n11. Enter 2016-08-11 and 2016-08-12 into the date inputs, select \"Submission date (original)\", and submit the search.\n12. Search for instances of the six words in the results to find the paper titled \"Phase transition from egalitarian to hierarchical societies driven by competition between cognitive and social constraints\", indicating that \"egalitarian\" is the correct answer.", "Number of steps": "12", "How long did this take?": "8 minutes", "Tools": "1. Web browser\n2. Image recognition tools (to identify and parse a figure with three axes)", "Number of tools": "2"}}
# random.seed(42)
random_samples = random.sample(json_QA, 1)
for sample in random_samples:
    print("=" * 50)
    print(f"Task ID: {sample['task_id']}")
    print(f"Question: {sample['Question']}")
    print(f"Level: {sample['Level']}")
    print(f"Final Answer: {sample['Final answer']}")
    print("Annotator Metadata: ")
    print("  ├── Steps: ")
    for step in sample["Annotator Metadata"]["Steps"].split("\n"):
        print(f"  │      ├── {step}")
    print(f"  ├── Number of steps: {sample['Annotator Metadata']['Number of steps']}")
    print(
        f"  ├── How long did this take?: {sample['Annotator Metadata']['How long did this take?']}"
    )
    print("  ├── Tools:")
    for tool in sample["Annotator Metadata"]["Tools"].split("\n"):
        print(f"  │      ├── {tool}")
    print(f"  └── Number of tools: {sample['Annotator Metadata']['Number of tools']}")
print("=" * 50)


Task ID: 0bdb7c40-671d-4ad1-9ce3-986b159c0ddc
Question: In NASA's Astronomy Picture of the Day on 2006 January 21, two astronauts are visible, with one appearing much smaller than the other. As of August 2023, out of the astronauts in the NASA Astronaut Group that the smaller astronaut was a member of, which one spent the least time in space, and how many minutes did he spend in space, rounded to the nearest minute? Exclude any astronauts who did not spend any time in space. Give the last name of the astronaut, separated from the number of minutes by a semicolon.
Level: 3
Final Answer: White; 5876
Annotator Metadata: 
  ├── Steps: 
  │      ├── 1. Use search engine to search for "NASA's Astronomy Picture of the Day 2006 January 21".
  │      ├── 2. Open the link to the image.
  │      ├── 3. Read the explanation to find that the image is of astronaut Charles "Pete" Conrad reflected in the helmet of astronaut Alan Bean.
  │      ├── 4. Observe that the smaller astronaut in the image is 

<div style="background-color:lightblue; color:black; font-weight:bold">

## 2. Creating chroma vector store

</div>


In [ ]:
# Necessary packages:
#   - langchain-chroma>=0.1.2
#   - langchain-huggingface
# Source:
#   http://python.langchain.com/docs/integrations/vectorstores/chroma/

embeddings = HuggingFaceEmbeddings(model_name="sentence-transformers/all-mpnet-base-v2")
vector_store = Chroma(
    collection_name="gaia_dataset",
    embedding_function=embeddings,
    persist_directory="./data/chroma_langchain_db",  # Where to save data locally, remove if not necessary
)


modules.json:   0%|          | 0.00/349 [00:00<?, ?B/s]

c:\Users\ee5011\Anaconda3\envs\llm-huggingface-agents-course-env\Lib\site-packages\huggingface_hub\file_download.py:143: UserWarning: `huggingface_hub` cache-system uses symlinks by default to efficiently store duplicated files but your machine does not support them in C:\Users\ee5011\.cache\huggingface\hub\models--sentence-transformers--all-mpnet-base-v2. Caching files will still work but in a degraded version that might require more space on your disk. This warning can be disabled by setting the `HF_HUB_DISABLE_SYMLINKS_WARNING` environment variable. For more details, see https://huggingface.co/docs/huggingface_hub/how-to-cache#limitations.
To support symlinks on Windows, you either need to activate Developer Mode or to run Python as an administrator. In order to activate developer mode, see this article: https://docs.microsoft.com/en-us/windows/apps/get-started/enable-your-device-for-development
  warnings.warn(message)


config_sentence_transformers.json:   0%|          | 0.00/116 [00:00<?, ?B/s]

README.md:   0%|          | 0.00/10.4k [00:00<?, ?B/s]

sentence_bert_config.json:   0%|          | 0.00/53.0 [00:00<?, ?B/s]

...

tokenizer_config.json:   0%|          | 0.00/363 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/466k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/239 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/190 [00:00<?, ?B/s]

In [ ]:
# wrap the metadata.jsonl's questions and answers into a list of document
docs = []
for i, sample in enumerate(json_QA):
    content = (
        f"Question : {sample['Question']}\n\nFinal answer : {sample['Final answer']}"
    )
    doc = Document(
        page_content=content,
        metadata={"source": sample["task_id"]},
        id=i,
    )
    docs.append(doc)

# upload the documents to the vector database
try:
    uuids = [str(uuid4()) for _ in range(len(docs))]
    vector_store.add_documents(documents=docs, ids=uuids)
except Exception as exception:
    print("Error inserting data into Supabase:", exception)

# ALTERNATIVE : Save the documents (a list of dict) into a csv file, and manually upload it to Supabase
# import pandas as pd
# df = pd.DataFrame(docs)
# df.to_csv('supabase_docs.csv', index=False)


<div style="background-color:lightblue; color:black; font-weight:bold">

## 3. Querying the database and converting to a retriever to search using

</div>


In [ ]:
# Querying directly from the vector database
query = "How many studio albums were published by Mercedes Sosa between 2000 and 2009 (included)? You can use the latest 2022 version of english wikipedia."

results = vector_store.similarity_search(
    query=query,
    k=2,
)
for res in results:
    print(f"* {res.page_content} [{res.metadata}]")


* Question : How many studio albums were published by Mercedes Sosa between 2000 and 2009 (included)? You can use the latest 2022 version of english wikipedia.

Final answer : 3 [{'source': '8e867cd7-cff9-4e6c-867a-ff5ddc2550be'}]
* Question : It is 1999. Before you party like it is 1999, please assist me in settling a bet.

Fiona Apple and Paula Cole released albums prior to 1999. Of these albums, which didn't receive a letter grade from Robert Christgau? Provide your answer as a comma delimited list of album titles, sorted alphabetically.

Final answer : Harbinger, Tidal [{'source': 'f46b4380-207e-4434-820b-f32ce04ae2a4'}]


In [ ]:
# Querying using a retriever
# Conver to a retriever
retriever = vector_store.as_retriever(
    search_type="mmr", search_kwargs={"k": 1, "fetch_k": 5}
)
results = retriever.invoke(input=query)


In [17]:
results

[Document(id='454c552a-b27f-4eba-ac9a-d37300e515cd', metadata={'source': '8e867cd7-cff9-4e6c-867a-ff5ddc2550be'}, page_content='Question : How many studio albums were published by Mercedes Sosa between 2000 and 2009 (included)? You can use the latest 2022 version of english wikipedia.\n\nFinal answer : 3')]